# Map of the Amazon basin fires and commodities production

The data about fires refer to the entire 2019 and were spotted by VIIRS 375m sensor, on board of the Suomi NPP/NOAA-20 satellite. VIIRS has a thermal band of 375m resolution, w.r.t., i.e. MODIS thermal resolution of 1000m.VIIRS spotted more than 1.45M fires only in Brazil. The dataset consists of all fires detected, reporting their geolocations, information about the acquisition (scan, track, refers to the actual size of the pixel, date, daynight about the time), the instrument and satellite used, they measured brightness in the I-4 and I-5 channels, and the type of fire I filtered the fires by type and confidence level (only vegetation fires and with confidence Nominal' or 'High'. Plotting requried downsampling the number of points/fires as they are in the order of magnitude of millions. I randomly downsampled, between the IQR range, the 5% of the total number and plotted on the map.
I added data about some of the human activities with the highest environmental impact, such as oil and mining sites, as well as indigeneous population areas. The data was downloaded from the Amazonian network of georeferenced socioenvironmental inforamtion (RAISG). I I filtered by country (Brazil) and randomly downsampled due to the order of magnitude of points that would have been plotted on the map.

In [66]:
import requests
import csv
import rasterio
import geopandas as gpd
import pandas as pd
import os
import zipfile
import folium
from folium.plugins import HeatMap
import branca
import numpy as np
from folium import IFrame
from folium.features import GeoJson, GeoJsonTooltip, GeoJsonPopup
import fiona
import branca.colormap as cm
import matplotlib.pyplot as plt
import matplotlib as mpl
from matplotlib.lines import Line2D
import seaborn as sns
from shapely import geometry
from shapely.ops import transform
import pyproj
%matplotlib inline

In [403]:
def plot_polygons(df, color, labels, layer):
    for i, row in df.iterrows():
        
        if type(row.geometry) == type(df_mining_illegal_pt_br.geometry.iloc[0]):
                folium.Circle((list(row.geometry.coords[0])[-1], list(row.geometry.coords[0])[0]),
                 radius=10000,
                 fill=True,
                 fill_color=color,
                opacity=0.5,
                 color='black',
                 stroke=True,
                 weight=1,
                 fill_opacity=0.8,
                tooltip=(row[labels][0])).add_to(layer)
                
        elif type(row.geometry) != type(df_oil_br[df_oil_br['index'] == 470]['geometry'].iloc[0]):
            if len(labels)==2:
                folium.Circle((list(row.geometry.exterior.coords)[0][-1], list(row.geometry.exterior.coords)[0][0]),
                             radius=10000,
                             fill=True,
                             fill_color=color,
                            opacity=0.5,
                             color='black',
                             stroke=True,
                             weight=1,
                             fill_opacity=0.8,
                             tooltip=(row[labels][0], row[labels][1])).add_to(layer)
            else:
                folium.Circle((list(row.geometry.exterior.coords)[0][-1], list(row.geometry.exterior.coords)[0][0]),
                 radius=10000,
                 fill=True,
                 fill_color=color,
                opacity=0.5,
                 color='black',
                 stroke=True,
                 weight=1,
                 fill_opacity=0.8,
                tooltip=(row[labels][0])).add_to(layer)

    layer.add_to(m)

In [12]:
# download fires spotted in Brazil by NASA VIIRS SUOMI in 2019
csv_url = 'https://firms.modaps.eosdis.nasa.gov/data/country/viirs-snpp/2019/viirs-snpp_2019_Brazil.csv'
req = requests.get(csv_url)
url_content = req.content
csv_file = open('./data/raw/geospatial/nasa-viirs-brazil-2019.csv', 'wb')

csv_file.write(url_content)
csv_file.close()

Unfortunately I didn't manage to download the Amazon basin shapefile (http://worldmap.harvard.edu/download/wfs/4682/zip?outputFormat=SHAPE-ZIP&service=WFS&request=GetFeature&format_options=charset%3AUTF-8&typename=geonode%3Aamapoly_ivb&version=1.0.0 and all files from RAISG (https://www.amazoniasocioambiental.org/en/maps/#!/download) directly from this notebook. Therefore, manual download is required.

All files must be saved in ./data/raw/geospatial/


In [70]:
# Manually download from:
# http://worldmap.harvard.edu/download/wfs/4682/zip?outputFormat=SHAPE-ZIP&service=WFS&request=GetFeature&format_options=charset%3AUTF-8&typename=geonode%3Aamapoly_ivb&version=1.0.0
# https://www.amazoniasocioambiental.org/en/download/zonas-mineras/
# https://www.amazoniasocioambiental.org/en/download/petroleo/
# https://www.amazoniasocioambiental.org/en/download/indigenous-territories/
# https://www.amazoniasocioambiental.org/en/download/illegal-mining/

In [29]:
os.mkdir('./reports/maps')
os.mkdir('./reports/assets/maps_analysis')
os.mkdir('./reports/assets')
save_path_assets = './reports/assets/maps_analysis'
save_path = './reports/maps/index.html'

In [64]:
def extract(file_to_extract, save_name_folder, path = './data/raw/geospatial/'):
    file_path = os.path.join(path, file_to_extract)
    save_path = os.path.join(path, save_name_folder)
    with zipfile.ZipFile(file_path, 'r') as z:
        z.extractall(save_path)

In [71]:
extract('mineria2020.zip', 'mineria2020')
extract('mineria2020.zip', 'mineria2020')
extract('mineria2020.zip', 'mineria2020')
extract('mineria2020.zip', 'mineria2020')
extract('amapoly_ivb.zip', 'amapoly_ivb')

In [3]:
mining_shp = './data/raw/geospatial/mineria2020/mineria.shp'
mining_illegal_shp_ln = './data/raw/geospatial/MineriaIlegal2020/MineriaIlegal_ln.shp'
mining_illegal_shp_pol = './data/raw/geospatial/MineriaIlegal2020/MineriaIlegal_pol.shp'
mining_illegal_shp_pt = './data/raw/geospatial/MineriaIlegal2020/MineriaIlegal_pt.shp'
territory_indigenos = './data/raw/geospatial/Tis_2020/Tis_TerritoriosIndigenas.shp'
oil = './data/raw/geospatial/petroleo2020/petroleo.shp'

In [72]:
amazon_gdf = gpd.read_file('./data/raw/geospatial/amapoly_ivb/amapoly_ivb.shp')

In [4]:
mining = gpd.read_file(mining_shp)
mining_br = mining[mining['pais'] == 'Brasil']

In [5]:
mining_illegal_ln = gpd.read_file(mining_illegal_shp_ln)
mining_illegal_ln_br = mining_illegal_ln[mining_illegal_ln['país'] == 'Brasil']

In [6]:
mining_illegal_pt = gpd.read_file(mining_illegal_shp_pt)
mining_illegal_pt_br = mining_illegal_pt[mining_illegal_pt['país'] == 'Brasil']

In [7]:
mining_illegal_pol = gpd.read_file(mining_illegal_shp_pol)
mining_illegal_pol_br = mining_illegal_pol[mining_illegal_pol['país'] == 'Brasil']

In [8]:
territory_indigenos_df = gpd.read_file(territory_indigenos)
indigenos_brasil = territory_indigenos_df[territory_indigenos_df['pais'] == 'Brasil']

In [9]:
oil_df = gpd.read_file(oil)
oil_brasil = oil_df[oil_df['pais'] == 'Brasil']

In [112]:
mining_br.shape, mining_illegal_ln_br.shape, mining_illegal_pt_br.shape, mining_illegal_pol_br.shape, indigenos_brasil.shape, oil_brasil.shape

((51981, 14), (9, 18), (323, 19), (2244, 20), (390, 23), (96, 16))

In [10]:
mining_br = mining_br.to_crs(epsg=4326)
mining_illegal_ln_br = mining_illegal_ln_br.to_crs(epsg=4326)
mining_illegal_pt_br = mining_illegal_pt_br.to_crs(epsg=4326)
mining_illegal_pol_br = mining_illegal_pol_br.to_crs(epsg=4326)
indigenos_brasil = indigenos_brasil.to_crs(epsg=4326)
oil_brasil = oil_brasil.to_crs(epsg=4326)

In [2]:
df = pd.read_csv('./data/raw/geospatial/nasa-viirs-brazil-2019.csv')

latitude  longitude  bright_ti4  scan  track    acq_date  acq_time  \
0       -3.597454 -38.859932      316.47  0.36   0.57  2019-01-01       322   
1       -3.592151 -38.859043      338.86  0.36   0.57  2019-01-01       322   
2       -3.591609 -38.862331      319.10  0.36   0.57  2019-01-01       322   
3       -5.577782 -35.229156      315.28  0.39   0.44  2019-01-01       322   
4       -4.924172 -37.982002      304.40  0.60   0.53  2019-01-01       322   
...           ...        ...         ...   ...    ...         ...       ...   
1451898  4.033268 -60.754417      330.15  0.40   0.37  2019-12-31      1719   
1451899  4.034374 -60.747162      335.39  0.40   0.37  2019-12-31      1719   
1451900  4.030655 -60.038990      332.13  0.39   0.36  2019-12-31      1719   
1451901  4.033988 -60.039536      341.46  0.39   0.36  2019-12-31      1719   
1451902 -7.782877 -72.787766      330.42  0.36   0.57  2019-12-31      1856   

        satellite instrument confidence  version  bright_ti5    frp daynight  \
0               N      VIIRS          n        1      290.32   1.24        N   
1               N      VIIRS          n        1      291.89   4.39        N   
2               N      VIIRS          n        1      291.63   4.86        N   
3               N      VIIRS          n        1      293.00   2.04        N   
4               N      VIIRS          n        1      291.99   1.75        N   
...           ...        ...        ...      ...         ...    ...      ...   
1451898         N      VIIRS          n        1      298.24   1.00        D   
1451899         N      VIIRS          n        1      300.27   7.39        D   
1451900         N      VIIRS          n        1      295.88   1.60        D   
1451901         N      VIIRS          n        1      300.54  12.21        D   
1451902         N      VIIRS          n        1      285.21   3.10        D   

         type  
0           3  
1           2  
2           2  
3           3  
4           0  
...       ...  
1451898     0  
1451899     0  
1451900     0  
1451901     0  
1451902     0  

[1451903 rows x 15 columns]

In [18]:
#sampling from IQR
df_sampled = df[(df['frp'] > df['frp'].quantile(q=0.05)) & (df['frp'] < df['frp'].quantile(q=0.75))]

df_sampled = df_sampled.sample(n=int(len(df_sampled)*0.01))
df_filtered = df[(df['confidence'] == 'n') | (df['confidence'] == 'h') & (df['type'] == 0)]
df_filtered_sampled = df_filtered[(df_filtered['frp'] > df_filtered['frp'].quantile(q=0.05)) & (df_filtered['frp'] < df_filtered['frp'].quantile(q=0.75))]
df_filtered_sampled = df_filtered_sampled.sample(n=int(len(df_filtered_sampled)*0.01))

In [144]:
current_palette = sns.color_palette('gist_earth')
first = current_palette[0]
second = current_palette[1]
third = current_palette[2]
sns.set_palette([second, third, first])

custom_lines = [Line2D([0], [0], color=third, lw=4),
                Line2D([0], [0], color=second, lw=4),
                Line2D([0], [0], color=first, lw=4)]

title = 'Histogram of Fires Spotted by VIIRS 375 m in Brazil by Type - 2019 (source:Suomi NPP satellite/NASA)'
type_pcg = pd.DataFrame(list(zip(df_sampled.type.value_counts(normalize=True).values*100,np.array([0,2,3]))), columns=['percentage','type'])
fig, ax = plt.subplots(dpi=200)
sns.barplot(x='type', y='percentage', data=type_pcg, palette=sns.set_palette([third, second, first]), ax=ax)
plt.title(title, size=14, pad=25)
ax.set_xlabel('Type of fire', size=18)
ax.set_ylabel('Percentage of total fires (%)', size=18)
ax.legend(custom_lines, ['Presumed vegetation fire', 'Other static land source', 'Offshore detection'])
plt.tight_layout(pad=10)
fig.savefig(os.path.join(save_path_assets, 'histogram_fires_spotted_viirs_by_type_2019.png'))

It is evident how the greatest majority of fires are classified as presumed vegetation fires.

In [148]:
plt.rcParams['figure.figsize'] = 15, 10
plt.rcParams['xtick.labelsize'] = 18
plt.rcParams['ytick.labelsize'] = 18
nbins = 12

data = [df_filtered_sampled['frp'].values]
bins = np.linspace(1,13,23)

cmap = plt.cm.inferno


hist, bin_edges = np.histogram(data, bins)
hist = (hist / sum(hist)) * 100
colors = cmap([((el - min(bins)) / (max(bins) - min(bins))) for el in bins])
fig, ax = plt.subplots(1,1)
ax.bar(bin_edges[:-1], hist, color=colors, alpha=0.8, width=0.52)

ax.set_xlim((0))
ax.set_xlabel('Fire Radiative Power(MW)', size=18)
ax.set_ylabel('Percentage of total fires (%)', size=18)
plt.title('Histogram of Fires Spotted by VIIRS 375 m in Brazil by their Radiative Power(MW) - 2019 (source:Suomi NPP satellite/NASA) ', size=14, pad=25)
plt.tight_layout(pad=10)
plt.savefig('./reports/assets/hist_fires_VIIRS_Brazil_2019.png')

In [7]:
locations = df_filtered_sampled[['latitude', 'longitude']]
locationlist = locations.values.tolist()
df_poi = df_filtered_sampled.reset_index()[poi]
location_data = location_frp[['latitude', 'longitude','frp']].to_numpy()
location_frp = df_poi[['latitude', 'longitude', 'frp']]

In [34]:
sampled_mining_br = mining_br.sample(frac=0.05)
filter_mining = sampled_mining_br.reset_index().apply(lambda x: x['geometry'].within(amazon_gdf['geometry'][0]), axis=1) # points of interest
df_mining_br = sampled_mining_br.reset_index()[filter_mining]
df_mining_br['type'] = 'Mining site' 

In [50]:
filter_oil = oil_brasil.reset_index().apply(lambda x: x['geometry'].within(amazon_gdf['geometry'][0]), axis=1) # points of interest
df_oil_br = oil_brasil.reset_index()[filter_oil]
df_oil_br['Type'] = 'Oil site'

In [51]:
filter_mining_illegal = mining_illegal_pol_br.reset_index().apply(lambda x: x['geometry'].within(amazon_gdf['geometry'][0]), axis=1) # points of interest
df_mining_illegal_pol_br = mining_illegal_pol_br.reset_index()[filter_mining_illegal]
df_mining_illegal_pol_br['type'] = 'Illegal mining site'

In [53]:
filter_mining_illegal = mining_illegal_pt_br.reset_index().apply(lambda x: x['geometry'].within(amazon_gdf['geometry'][0]), axis=1) # points of interest
df_mining_illegal_pt_br = mining_illegal_pt_br.reset_index()[filter_mining_illegal]
df_mining_illegal_pt_br['type'] = 'Illegal mining site'

In [54]:
filter_indigenos_brasil = indigenos_brasil.reset_index().apply(lambda x: x['geometry'].within(amazon_gdf['geometry'][0]), axis=1) # points of interest
df_indigenos_brasil = indigenos_brasil.reset_index()[filter_indigenos_brasil]
df_indigenos_brasil['type'] = 'Indigenous people area'

In [605]:
m = folium.Map(location = [-3.65, -63],
               tiles = 'Stamen Terrain',
               zoom_start = 5.3)



layer_1 = folium.FeatureGroup(name='Legal mines')
plot_polygons(df_mining_br,'#00FFD8', ['type','tipo_miner'], layer_1)
layer_2 = folium.FeatureGroup(name='Oil sites')
plot_polygons(df_oil_br, '#F000FF', ['Type','cia'], layer_2)
layer_3 = folium.FeatureGroup(name='Illegal mines')
plot_polygons(df_mining_illegal_pol_br, '#CDFF00', ['type'], layer_3)
plot_polygons(df_mining_illegal_pt_br, '#CDFF00', ['type'], layer_3)
layer_4 = folium.FeatureGroup(name='Indigenous people area')
plot_polygons(df_indigenos_brasil, '#FFFFFF', ['type'], layer_4)



gradient = {0.08:'rgba(0, 0, 3, 1)',0.33: 'rgba(65, 9, 103, 1)',0.5: 'rgba(147, 37, 103, 1)', 0.67:'rgba(220, 80, 57, 1)', 0.83:'rgba(251, 164, 10, 1)', 1:'rgba(252, 254, 164, 1)'}
# plot heatmap
colormap = cm.LinearColormap(colors=['#000003', '#410967', '#932567', '#DC5039', '#FBA40A', '#FCFEA4'], index=[1, 4, 6, 8, 10, 12], vmin=1,vmax=12, caption='Fire Radiative Power (MW)')

m.add_child(HeatMap(location_data, 
                    radius=10, 
                    min_opacity=0.35,
                    max_zoom=10,
                    blur=8,
                    name='Fires(MW)', 
                    gradient=gradient))
m.add_child(colormap)
folium.LayerControl().add_to(m)
legend_html = '''
{% macro html(this, kwargs) %}
<div style="
    position: fixed; 
    bottom: 50px;
    left: 50px;
    width: 300px;
    height: 175px;
    z-index:9980;
    font-size:14px;
    ">
    <p style="font-weight: bold;"><a style="color:#00FFD8;font-size:150%;margin-left:20px;">&#x2B24;</a>&emsp;Legal mines</p>
    <p style="font-weight: bold;"><a style="color:#F000FF;font-size:150%;margin-left:20px;">&#x2B24;</a>&emsp;Oil sites</p>
    <p style="font-weight: bold;"><a style="color:#CDFF00;font-size:150%;margin-left:20px;">&#x2B24;</a>&emsp;Illegal mines</p>
    <p style="font-weight: bold;"><a style="color:#FFFFFF;font-size:150%;margin-left:20px;">&#x2B24;</a>&emsp;Indigenous people area</p>
</div>
<div style="
    position: fixed; 
    bottom: 50px;
    left: 50px;
    width: 200px;
    height: 200px; 
    z-index:9960;
    font-size:14px;
    background-color: #ffffff;

    opacity: 0.3;
    ">
</div>
{% endmacro %}
'''
legend = branca.element.MacroElement()
legend._template = branca.element.Template(legend_html)
m.get_root().add_child(legend)

In [611]:
m.save(save_path)

The heatmap shows fires and their radiative power, expressed in MW, which is the rate of emitted radiative energy by the fire at the time of the observation. It is possible to immediately identify an arch of fires, covering the sourthern part of the Amazon basin. In the northern state of Roraima, there is another cluster of fires, as well, it is possible to see a series of fires starting from the delta of the Amazon river, up until Manaus. 

It is significant to highlight how, confirming qualitative news available on media, that there is some significant overlapping between fires and mining sites in particular. Unfortunately, there was no data on farming activities, considering that they are ranked as one of the main causes of deforestation through fires.